In [1]:
!pip install -U -q langchain langchain-openai langchain_core langchain-community langchainhub openai

In [2]:
!pip install -qU qdrant-client pymupdf pandas

In [21]:
import os
import openai
import getpass
import chainlit as cl
from langchain_community.document_loaders import PyMuPDFLoader
from langchain_openai import OpenAIEmbeddings
from langchain_openai import ChatOpenAI
from langchain_community.vectorstores import Qdrant
from langchain.prompts import ChatPromptTemplate

from dotenv import load_dotenv
from operator import itemgetter
from langchain_huggingface import HuggingFaceEndpoint
from langchain_community.document_loaders import TextLoader
from langchain_text_splitters import RecursiveCharacterTextSplitter
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain_community.vectorstores import FAISS
from langchain_huggingface import HuggingFaceEndpointEmbeddings
from langchain_core.prompts import PromptTemplate
from langchain.schema.output_parser import StrOutputParser
from langchain.schema.runnable import RunnablePassthrough
from langchain.schema.runnable.config import RunnableConfig

#Load environment variables
load_dotenv()
OPENAI_API_KEY = os.environ["OPENAI_API_KEY"]


#Load 10-K PDF and split into chunks
loader = PyMuPDFLoader (
    "https://www.hillrom.com/content/dam/hillrom-aem/us/en/sap-documents/LIT/80026/80026025LITPDF.pdf"
)

documents = loader.load()


text_splitter = RecursiveCharacterTextSplitter(
    chunk_size = 1000,
    chunk_overlap = 100
)

documents = text_splitter.split_documents(documents)

#Load embeddings model - we'll use OpenAI's text-embedding-3-small
embeddings = OpenAIEmbeddings(
    model="text-embedding-3-small"
)

#Create QDrant vector store
qdrant_vector_store = Qdrant.from_documents(
    documents,
    embeddings,
    location=":memory:",
    collection_name="WelchAllynConnex6000VSMServiceManual",
)

#Create Retriever
retriever = qdrant_vector_store.as_retriever()

#Create Prompt Template
template = """Answer the question based only on the following context. If you cannot answer the question with the context, please respond with 'I don't know':

Context:
{context}

Question:
{question}
"""

prompt = ChatPromptTemplate.from_template(template)

#Choose LLM - we'll use gpt-4o.
primary_llm = ChatOpenAI(model_name="gpt-4o", temperature=0)

2024-07-18 14:47:19 - HTTP Request: POST https://api.openai.com/v1/embeddings "HTTP/1.1 200 OK"
2024-07-18 14:47:20 - HTTP Request: POST https://api.openai.com/v1/embeddings "HTTP/1.1 200 OK"
2024-07-18 14:47:21 - HTTP Request: POST https://api.openai.com/v1/embeddings "HTTP/1.1 200 OK"
2024-07-18 14:47:21 - HTTP Request: POST https://api.openai.com/v1/embeddings "HTTP/1.1 200 OK"
2024-07-18 14:47:22 - HTTP Request: POST https://api.openai.com/v1/embeddings "HTTP/1.1 200 OK"
2024-07-18 14:47:23 - HTTP Request: POST https://api.openai.com/v1/embeddings "HTTP/1.1 200 OK"
2024-07-18 14:47:24 - HTTP Request: POST https://api.openai.com/v1/embeddings "HTTP/1.1 200 OK"
2024-07-18 14:47:25 - HTTP Request: POST https://api.openai.com/v1/embeddings "HTTP/1.1 200 OK"
2024-07-18 14:47:25 - HTTP Request: POST https://api.openai.com/v1/embeddings "HTTP/1.1 200 OK"
2024-07-18 14:47:26 - HTTP Request: POST https://api.openai.com/v1/embeddings "HTTP/1.1 200 OK"
2024-07-18 14:47:29 - HTTP Request: POST

In [24]:
retrieved_documents = retriever.invoke("How do I specify advanced alarm settings?")

2024-07-18 14:50:04 - HTTP Request: POST https://api.openai.com/v1/embeddings "HTTP/1.1 200 OK"


In [25]:
for doc in retrieved_documents:
  print(doc)

page_content='tab in the Device Status area.
Enable NTP
Select to use the NTP server for time
synchronization rather than the episodic host.
Host name or IP address
Enter the host name, IP address, or domain name of
the NTP server.
Test
Touch Test to test the connection to the NTP
server.
Information messages indicate that a test is in
progress and then the result of the test (pass or fail).
4.
Do one of the following:
•
To continue in the Advanced settings, touch another tab.
•
To exit the Advanced settings and return to the Home tab, touch Exit.
Specify advanced alarm settings
1.
Access the Advanced settings.
a.
Touch the Settings tab.
b.
Touch the Advanced tab.
c.
Touch Enter password.
d.
Enter your password and touch OK.
The General tab appears.
2.
Touch the Alarms tab.
3.
Specify settings.
24 Advanced settings' metadata={'source': 'https://www.hillrom.com/content/dam/hillrom-aem/us/en/sap-documents/LIT/80026/80026025LITPDF.pdf', 'file_path': 'https://www.hillrom.com/content/dam/hi

In [26]:
primary_llm = ChatOpenAI(model_name="gpt-4o", temperature=0)

retrieval_augmented_chain = (
        # INVOKE CHAIN WITH: {"question" : "<<SOME USER QUESTION>>"}
        # "question" : populated by getting the value of the "question" key
        # "context"  : populated by getting the value of the "question" key and chaining it into the base_retriever
        {"context": itemgetter("question") | retriever, "question": itemgetter("question")}
        | prompt | primary_llm
    )

In [28]:
question = "How do I specify advanced alarm settings?"

result = retrieval_augmented_chain.invoke({"question" : question})


2024-07-18 14:52:25 - HTTP Request: POST https://api.openai.com/v1/embeddings "HTTP/1.1 200 OK"
2024-07-18 14:52:27 - HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"


In [ ]:

print(result["response"].content)

In [29]:
print(result)

content='To specify advanced alarm settings, follow these steps:\n\n1. Access the Advanced settings:\n   a. Touch the Settings tab.\n   b. Touch the Advanced tab.\n   c. Touch Enter password.\n   d. Enter your password and touch OK. The General tab appears.\n2. Touch the Alarms tab.\n3. Specify settings.' response_metadata={'token_usage': {'completion_tokens': 68, 'prompt_tokens': 2027, 'total_tokens': 2095}, 'model_name': 'gpt-4o-2024-05-13', 'system_fingerprint': 'fp_c4e5b6fa31', 'finish_reason': 'stop', 'logprobs': None} id='run-e022a522-caec-4748-b093-24ca2b030a81-0' usage_metadata={'input_tokens': 2027, 'output_tokens': 68, 'total_tokens': 2095}
